In [11]:
import logging
logging.basicConfig(level=logging.ERROR)

In [12]:
from pyspark.sql.types import StructType, StructField, StringType
from pyspark.sql import SparkSession

# SparkSession oluşturma
spark = SparkSession.builder \
    .appName("SummarizationApp") \
    .config("spark.some.config.option", "some-value") \
    .getOrCreate()

# Şema tanımı
schema = StructType([
    StructField("id", StringType(), True),
    StructField("article", StringType(), True),
    StructField("highlights", StringType(), True)
])

# Şemayı kullanarak HDFS'teki CSV dosyalarını okuma
train_data = spark.read.schema(schema).option("header", "true").csv("hdfs:///cnn_dailymail/train.csv")
test_data = spark.read.schema(schema).option("header", "true").csv("hdfs:///cnn_dailymail/test.csv")
validation_data = spark.read.schema(schema).option("header", "true").csv("hdfs:///cnn_dailymail/validation.csv")

# İlk 5 satırı görüntüleme (opsiyonel)
train_data.show(5)
test_data.show(5)
validation_data.show(5)


+--------------------+--------------------+--------------------+
|                  id|             article|          highlights|
+--------------------+--------------------+--------------------+
|0001d1afc246a7964...|By . Associated P...|Bishop John Folda...|
|He contracted the...|                null|                null|
|Church members in...| Grand Forks and ...|                null|
|0002095e55fcbd3a2...|"(CNN) -- Ralph M...|"" of using his r...|
|          Ralph Mata| an internal affa...| allegedly helped...|
+--------------------+--------------------+--------------------+
only showing top 5 rows

+--------------------+--------------------+--------------------+
|                  id|             article|          highlights|
+--------------------+--------------------+--------------------+
|92c514c913c0bdfe2...|Ever noticed how ...|Experts question ...|
|U.S consumer advi...|                null|                null|
|Safety tests cond...|                null|                null|


In [13]:
# 1. 'id' ve 'highlights' sütunlarını kaldırma
train_data = train_data.drop("id")
test_data = test_data.drop("id")
validation_data = validation_data.drop("id")

In [14]:
# Geçerli makale ve özetlerin olduğu satırları filtrele
cleaned_train_data = train_data.filter(train_data.article.isNotNull() & train_data.highlights.isNotNull())
cleaned_test_data = test_data.filter(test_data.article.isNotNull() & test_data.highlights.isNotNull())
cleaned_validation_data = validation_data.filter(validation_data.article.isNotNull() & validation_data.highlights.isNotNull())

cleaned_train_data.show(5)
cleaned_test_data.show(5)
cleaned_validation_data.show(5)


+--------------------+--------------------+
|             article|          highlights|
+--------------------+--------------------+
|By . Associated P...|Bishop John Folda...|
|"(CNN) -- Ralph M...|"" of using his r...|
| an internal affa...| allegedly helped...|
|A drunk driver wh...|Craig Eccleston-T...|
|(CNN) -- With a b...|Nina dos Santos s...|
+--------------------+--------------------+
only showing top 5 rows

+--------------------+--------------------+
|             article|          highlights|
+--------------------+--------------------+
|Ever noticed how ...|Experts question ...|
|A drunk teenage b...|Drunk teenage boy...|
|                  17| ran towards anim...|
|Dougie Freedman i...|Nottingham Forest...|
|Liverpool target ...|Fiorentina goalke...|
+--------------------+--------------------+
only showing top 5 rows

+--------------------+--------------------+
|             article|          highlights|
+--------------------+--------------------+
|Sally Forrest, an...|Sall

In [15]:
from pyspark.sql.functions import regexp_replace

# Sadece alfabedik karakterleri ve boşlukları koru
cleaned_train_data = cleaned_train_data.withColumn("cleaned_article", regexp_replace(cleaned_train_data.article, "[^a-zA-Z\s]", ""))
cleaned_train_data = cleaned_train_data.withColumn("cleaned_highlights", regexp_replace(cleaned_train_data.highlights, "[^a-zA-Z\s]", ""))

cleaned_test_data = cleaned_test_data.withColumn("cleaned_article", regexp_replace(cleaned_test_data.article, "[^a-zA-Z\s]", ""))
cleaned_test_data = cleaned_test_data.withColumn("cleaned_highlights", regexp_replace(cleaned_test_data.highlights, "[^a-zA-Z\s]", ""))

cleaned_validation_data = cleaned_validation_data.withColumn("cleaned_article", regexp_replace(cleaned_validation_data.article, "[^a-zA-Z\s]", ""))
cleaned_validation_data = cleaned_validation_data.withColumn("cleaned_highlights", regexp_replace(cleaned_validation_data.highlights, "[^a-zA-Z\s]", ""))

cleaned_train_data.show(5)
cleaned_test_data.show(5)
cleaned_validation_data.show(5)


+--------------------+--------------------+--------------------+--------------------+
|             article|          highlights|     cleaned_article|  cleaned_highlights|
+--------------------+--------------------+--------------------+--------------------+
|By . Associated P...|Bishop John Folda...|By  Associated Pr...|Bishop John Folda...|
|"(CNN) -- Ralph M...|"" of using his r...|CNN  Ralph Mata w...| of using his rol...|
| an internal affa...| allegedly helped...| an internal affa...| allegedly helped...|
|A drunk driver wh...|Craig Eccleston-T...|A drunk driver wh...|Craig EcclestonTo...|
|(CNN) -- With a b...|Nina dos Santos s...|CNN  With a breez...|Nina dos Santos s...|
+--------------------+--------------------+--------------------+--------------------+
only showing top 5 rows

+--------------------+--------------------+--------------------+--------------------+
|             article|          highlights|     cleaned_article|  cleaned_highlights|
+--------------------+-------

In [16]:
from pyspark.sql.functions import lower

cleaned_train_data = cleaned_train_data.withColumn("cleaned_article", lower(cleaned_train_data.cleaned_article))
cleaned_train_data = cleaned_train_data.withColumn("cleaned_highlights", lower(cleaned_train_data.cleaned_highlights))

cleaned_test_data = cleaned_test_data.withColumn("cleaned_article", lower(cleaned_test_data.cleaned_article))
cleaned_test_data = cleaned_test_data.withColumn("cleaned_highlights", lower(cleaned_test_data.cleaned_highlights))

cleaned_validation_data = cleaned_validation_data.withColumn("cleaned_article", lower(cleaned_validation_data.cleaned_article))
cleaned_validation_data = cleaned_validation_data.withColumn("cleaned_highlights", lower(cleaned_validation_data.cleaned_highlights))


In [17]:
from pyspark.ml.feature import Tokenizer, StopWordsRemover

# Önce metni token'lere ayırın
tokenizer = Tokenizer(inputCol="cleaned_article", outputCol="tokenized_article")
tokenized_train_data = tokenizer.transform(cleaned_train_data)
tokenized_test_data = tokenizer.transform(cleaned_test_data)
tokenized_validation_data = tokenizer.transform(cleaned_validation_data)

tokenizer.setParams(inputCol="cleaned_highlights", outputCol="tokenized_highlights")
tokenized_train_data = tokenizer.transform(tokenized_train_data)
tokenized_test_data = tokenizer.transform(tokenized_test_data)
tokenized_validation_data = tokenizer.transform(tokenized_validation_data)

# Ardından durma kelimelerini kaldırın
remover = StopWordsRemover(inputCol="tokenized_article", outputCol="filtered_article")
filtered_train_data = remover.transform(tokenized_train_data)
filtered_test_data = remover.transform(tokenized_test_data)
filtered_validation_data = remover.transform(tokenized_validation_data)

remover.setParams(inputCol="tokenized_highlights", outputCol="filtered_highlights")
filtered_train_data = remover.transform(filtered_train_data)
filtered_test_data = remover.transform(filtered_test_data)
filtered_validation_data = remover.transform(filtered_validation_data)

# Tokenized ve filtered sütunlarını da göster
filtered_train_data.select("cleaned_article", "tokenized_article", "filtered_article").show(5)
filtered_test_data.select("cleaned_article", "tokenized_article", "filtered_article").show(5)
filtered_validation_data.select("cleaned_article", "tokenized_article", "filtered_article").show(5)



+--------------------+--------------------+--------------------+
|     cleaned_article|   tokenized_article|    filtered_article|
+--------------------+--------------------+--------------------+
|by  associated pr...|[by, , associated...|[, associated, pr...|
|cnn  ralph mata w...|[cnn, , ralph, ma...|[cnn, , ralph, ma...|
| an internal affa...|[, an, internal, ...|[, internal, affa...|
|a drunk driver wh...|[a, drunk, driver...|[drunk, driver, k...|
|cnn  with a breez...|[cnn, , with, a, ...|[cnn, , breezy, s...|
+--------------------+--------------------+--------------------+
only showing top 5 rows

+--------------------+--------------------+--------------------+
|     cleaned_article|   tokenized_article|    filtered_article|
+--------------------+--------------------+--------------------+
|ever noticed how ...|[ever, noticed, h...|[ever, noticed, p...|
|a drunk teenage b...|[a, drunk, teenag...|[drunk, teenage, ...|
|                    |                  []|                  []|


In [18]:
filtered_train_data_500 = filtered_train_data.limit(500)
filtered_train_data_500.show(5)

+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|             article|          highlights|     cleaned_article|  cleaned_highlights|   tokenized_article|tokenized_highlights|    filtered_article| filtered_highlights|
+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+--------------------+
|By . Associated P...|Bishop John Folda...|by  associated pr...|bishop john folda...|[by, , associated...|[bishop, john, fo...|[, associated, pr...|[bishop, john, fo...|
|"(CNN) -- Ralph M...|"" of using his r...|cnn  ralph mata w...| of using his rol...|[cnn, , ralph, ma...|[, of, using, his...|[cnn, , ralph, ma...|[, using, role, p...|
| an internal affa...| allegedly helped...| an internal affa...| allegedly helped...|[, an, internal, ...|[, allegedly, hel...|[, internal, affa...|[,

In [19]:
# 'filtered_article' için listeler oluşturma
filtered_article_list = [row['filtered_article'] for row in filtered_train_data_500.collect()]

# 'filtered_highlights' için listeler oluşturma
filtered_highlights_list = [row['filtered_highlights'] for row in filtered_train_data_500.collect()]

from keras.preprocessing.text import Tokenizer

# Tokenizer'ı başlatma
tf_tokenizer = Tokenizer(num_words=5000, oov_token='<OOV>')
tf_tokenizer.fit_on_texts(filtered_article_list + filtered_highlights_list)

# Tokenleri sayısal formata dönüştürme
article_sequences = tf_tokenizer.texts_to_sequences(filtered_article_list)
highlights_sequences = tf_tokenizer.texts_to_sequences(filtered_highlights_list)


In [23]:
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, LSTM, Dense

# Hiperparametreler
embedding_dim = 256
hidden_units = 512

# Encoder
encoder_inputs = Input(shape=(None, vocab_size))
encoder = LSTM(hidden_units, return_state=True)
encoder_outputs, state_h, state_c = encoder(encoder_inputs)
encoder_states = [state_h, state_c]

# Decoder
decoder_inputs = Input(shape=(None, vocab_size))
decoder_lstm = LSTM(hidden_units, return_sequences=True, return_state=True)
decoder_outputs, _, _ = decoder_lstm(decoder_inputs, initial_state=encoder_states)
decoder_dense = Dense(vocab_size, activation='softmax')
decoder_outputs = decoder_dense(decoder_outputs)

# Seq2Seq Model
model = Model([encoder_inputs, decoder_inputs], decoder_outputs)

# Modeli derleme
model.compile(optimizer='rmsprop', loss='categorical_crossentropy', metrics=['accuracy'])


2023-10-03 00:57:11.372541: W tensorflow/core/framework/cpu_allocator_impl.cc:82] Allocation of 40960000 exceeds 10% of free system memory.
2023-10-03 00:57:11.461511: W tensorflow/core/framework/cpu_allocator_impl.cc:82] Allocation of 40960000 exceeds 10% of free system memory.
2023-10-03 00:57:11.477142: W tensorflow/core/framework/cpu_allocator_impl.cc:82] Allocation of 40960000 exceeds 10% of free system memory.
2023-10-03 00:57:11.932382: W tensorflow/core/framework/cpu_allocator_impl.cc:82] Allocation of 40960000 exceeds 10% of free system memory.
2023-10-03 00:57:11.987195: W tensorflow/core/framework/cpu_allocator_impl.cc:82] Allocation of 40960000 exceeds 10% of free system memory.


In [20]:
from keras.models import Model
from keras.layers import Input, LSTM, Dense, Embedding

# Hyperparametreler
embedding_dim = 128
lstm_units = 256
vocab_size = 5000

# Encoder
encoder_inputs = Input(shape=(None,))
encoder_embedding = Embedding(vocab_size, embedding_dim)(encoder_inputs)
encoder_lstm = LSTM(lstm_units, return_state=True)
encoder_outputs, state_h, state_c = encoder_lstm(encoder_embedding)
encoder_states = [state_h, state_c]

# Decoder
decoder_inputs = Input(shape=(None,))
decoder_embedding = Embedding(vocab_size, embedding_dim)(decoder_inputs)
decoder_lstm = LSTM(lstm_units, return_sequences=True, return_state=True)
decoder_outputs, _, _ = decoder_lstm(decoder_embedding, initial_state=encoder_states)
decoder_dense = Dense(vocab_size, activation='softmax')
decoder_outputs = decoder_dense(decoder_outputs)

# Modeli tanımlama
model = Model([encoder_inputs, decoder_inputs], decoder_outputs)


2023-10-03 00:51:13.270279: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory
2023-10-03 00:51:13.271751: W tensorflow/stream_executor/cuda/cuda_driver.cc:263] failed call to cuInit: UNKNOWN ERROR (303)
2023-10-03 00:51:13.272641: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (muhammad-VM): /proc/driver/nvidia/version does not exist
2023-10-03 00:51:13.277881: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [21]:
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
model.fit([article_sequences, highlights_sequences], highlights_sequences, batch_size=64, epochs=50, validation_split=0.1)


ValueError: `validation_split` is only supported for Tensors or NumPy arrays, found following types in the input: [<class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, 

In [22]:
import numpy as np

article_sequences = np.array(article_sequences)
highlights_sequences = np.array(highlights_sequences)


/tmp/ipykernel_55435/3226080710.py:3: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  article_sequences = np.array(article_sequences)
/tmp/ipykernel_55435/3226080710.py:4: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  highlights_sequences = np.array(highlights_sequences)


In [ ]:
# Özetlerin listesi
summaries_list = [row['highlights'] for row in filtered_train_data_500.collect()] # Eğer özet sütununuzun adı 'summary' değilse, doğru ismi kullanın.

# Özetler için sayısal tokenleri oluşturma
summary_sequences = tf_tokenizer.texts_to_sequences(summaries_list)


In [ ]:
from keras.models import Model
from keras.layers import Input, LSTM, Dense, Embedding

# Hyperparametreler
embedding_dim = 128
lstm_units = 256
vocab_size = 5000

# Encoder
encoder_inputs = Input(shape=(None,))
encoder_embedding = Embedding(vocab_size, embedding_dim)(encoder_inputs)
encoder_lstm = LSTM(lstm_units, return_state=True)
encoder_outputs, state_h, state_c = encoder_lstm(encoder_embedding)
encoder_states = [state_h, state_c]

# Decoder
decoder_inputs = Input(shape=(None,))
decoder_embedding = Embedding(vocab_size, embedding_dim)(decoder_inputs)
decoder_lstm = LSTM(lstm_units, return_sequences=True, return_state=True)
decoder_outputs, _, _ = decoder_lstm(decoder_embedding, initial_state=encoder_states)
decoder_dense = Dense(vocab_size, activation='softmax')
decoder_outputs = decoder_dense(decoder_outputs)

# Modeli tanımlama
model = Model([encoder_inputs, decoder_inputs], decoder_outputs)


In [24]:
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])
model.fit([input_sequences, summary_sequences], summary_sequences, batch_size=64, epochs=50, validation_split=0.1)


ValueError: `validation_split` is only supported for Tensors or NumPy arrays, found following types in the input: [<class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, <class 'int'>, 

In [15]:
import tensorflow as tf
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences

# 'filtered_article' sütununu bir Python listesi olarak al
articles_list = [row.filtered_article for row in filtered_train_data_500.collect()]

# Tokenizasyon
tokenizer = Tokenizer(num_words=5000, oov_token='<OOV>')
tokenizer.fit_on_texts(articles_list)

# Veriyi sayısal formata dönüştürme
input_sequences = tokenizer.texts_to_sequences(input_texts) # giriş metinleri (makaleler)
output_sequences = tokenizer.texts_to_sequences(output_texts) # çıktı metinleri (özetler)

# Padding (uzunlukları eşitleme)
input_padded = pad_sequences(input_sequences, padding='post', maxlen=200)
output_padded = pad_sequences(output_sequences, padding='post', maxlen=50)

# Seq2Seq model oluşturma
model = tf.keras.Sequential([
    tf.keras.layers.Embedding(5000, 64, input_length=200),
    tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(64, return_sequences=True)),
    tf.keras.layers.Bidirectional(tf.keras.layers.LSTM(32)),
    tf.keras.layers.Dense(5000, activation='softmax')
])

model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

# Modeli eğitme
model.fit(input_padded, output_padded, epochs=10, batch_size=64)


NameError: name 'input_texts' is not defined

In [9]:
pip install nltk

Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.


In [10]:
import nltk
from pyspark.sql.functions import udf
from pyspark.sql.types import ArrayType, StringType

# NLTK'nin PorterStemmer'ını kullanarak bir stemming işlevi tanımlayın
stemmer = nltk.PorterStemmer()

def stem_words(words):
    return [stemmer.stem(word) for word in words]

# Stemming işlevini bir UDF olarak kaydedin
stemming_udf = udf(stem_words, ArrayType(StringType()))


In [11]:
def stem_data(df):
    df = df.withColumn("stemmed_article", stemming_udf(df["tokenized_article"]))
    df = df.withColumn("stemmed_highlights", stemming_udf(df["tokenized_highlights"]))
    return df

stemmed_train_data = stem_data(filtered_train_data)
stemmed_test_data = stem_data(filtered_test_data)
stemmed_validation_data = stem_data(filtered_validation_data)


In [12]:
# Her bir kelimede benzersiz tokenleri ve indeksleri elde edin
all_tokens = set()
for row in stemmed_train_data.rdd.collect():
    all_tokens.update(row.stemmed_article + row.stemmed_highlights)

# Token - indeks ve indeks - token eşleştirmesi oluşturun
token_to_index = {token: idx for idx, token in enumerate(all_tokens)}
index_to_token = {idx: token for token, idx in token_to_index.items()}

# Veri setlerini oluşturun
def generate_data(dataset):
    encoder_input_data = []
    decoder_input_data = []
    decoder_target_data = []

    for row in dataset.rdd.collect():
        # Encoder verisi
        encoder_input = [token_to_index[token] for token in row.stemmed_article]
        encoder_input_data.append(encoder_input)

        # Decoder verisi
        decoder_input = [token_to_index['_START_']] + [token_to_index[token] for token in row.stemmed_highlights]
        decoder_target = [token_to_index[token] for token in row.stemmed_highlights] + [token_to_index['_END_']]

        decoder_input_data.append(decoder_input)
        decoder_target_data.append(decoder_target)

    return np.array(encoder_input_data), np.array(decoder_input_data), np.array(decoder_target_data)

# Veri setlerini oluşturun
encoder_input_data, decoder_input_data, decoder_target_data = generate_data(stemmed_train_data)


2023-10-02 21:37:49,299 WARN python.PythonUDFRunner: Detected deadlock while completing task 1.0 in stage 15 (TID 16): Attempting to kill Python Worker
2023-10-02 21:37:49,334 ERROR executor.Executor: Exception in task 1.0 in stage 15.0 (TID 16)
java.lang.OutOfMemoryError: GC overhead limit exceeded
	at net.razorvine.pickle.PickleUtils.integer_to_bytes(PickleUtils.java:154)
	at net.razorvine.pickle.Pickler.writeMemo(Pickler.java:222)
	at net.razorvine.pickle.Pickler.put_string(Pickler.java:710)
	at net.razorvine.pickle.Pickler.dispatch(Pickler.java:312)
	at net.razorvine.pickle.Pickler.save(Pickler.java:193)
	at net.razorvine.pickle.Pickler.put_collection(Pickler.java:415)
	at net.razorvine.pickle.Pickler.dispatch(Pickler.java:371)
	at net.razorvine.pickle.Pickler.save(Pickler.java:193)
	at org.apache.spark.sql.execution.python.EvaluatePython$RowPickler.pickle(EvaluatePython.scala:271)
	at net.razorvine.pickle.Pickler.dispatch(Pickler.java:305)
	at net.razorvine.pickle.Pickler.save(Pic

ERROR:root:Exception while sending command.
Traceback (most recent call last):
  File "/usr/lib/python3/dist-packages/IPython/core/interactiveshell.py", line 3457, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "/tmp/ipykernel_49998/1449724943.py", line 3, in <module>
    for row in stemmed_train_data.rdd.collect():
  File "/usr/local/spark/python/pyspark/rdd.py", line 950, in collect
    sock_info = self.ctx._jvm.PythonRDD.collectAndServe(self._jrdd.rdd())
  File "/usr/local/spark/python/lib/py4j-0.10.9.5-src.zip/py4j/java_gateway.py", line 1321, in __call__
    return_value = get_return_value(
  File "/usr/local/spark/python/pyspark/sql/utils.py", line 111, in deco
    return f(*a, **kw)
  File "/usr/local/spark/python/lib/py4j-0.10.9.5-src.zip/py4j/protocol.py", line 326, in get_return_value
    raise Py4JJavaError(
py4j.protocol.Py4JJavaError: <unprintable Py4JJavaError object>

During handling of the above exception, another exception occurred:

Traceback

ConnectionRefusedError: [Errno 111] Connection refused

In [ ]:
import tensorflow as tf
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, LSTM, Dense

# Hiperparametreler
BATCH_SIZE = 64
EPOCHS = 100
LATENT_DIM = 256  # LSTM ünitelerinin sayısı
NUM_SAMPLES = len(encoder_input_data)  # Eğitim örneklerinin sayısı
MAX_ENCODER_SEQ_LENGTH = max([len(txt) for txt in encoder_input_data])
MAX_DECODER_SEQ_LENGTH = max([len(txt) for txt in decoder_input_data])
NUM_TOKENS = len(all_tokens)


In [ ]:
# Encoder
encoder_inputs = Input(shape=(None, NUM_TOKENS))
encoder = LSTM(LATENT_DIM, return_state=True)
encoder_outputs, state_h, state_c = encoder(encoder_inputs)
encoder_states = [state_h, state_c]

# Decoder
decoder_inputs = Input(shape=(None, NUM_TOKENS))
decoder_lstm = LSTM(LATENT_DIM, return_sequences=True, return_state=True)
decoder_outputs, _, _ = decoder_lstm(decoder_inputs, initial_state=encoder_states)
decoder_dense = Dense(NUM_TOKENS, activation='softmax')
decoder_outputs = decoder_dense(decoder_outputs)

# Model
model = Model([encoder_inputs, decoder_inputs], decoder_outputs)

# Derleme
model.compile(optimizer='rmsprop', loss='categorical_crossentropy', metrics=['accuracy'])

# Modeli eğitin
model.fit([encoder_input_data, decoder_input_data], decoder_target_data,
          batch_size=BATCH_SIZE,
          epochs=EPOCHS,
          validation_split=0.2)
